In [24]:
import retrieval.cache as cache
import signals.curve as curve
import signals.simple_scalping as simple_scalping

import numpy as np
import pandas as pd
import pandas_ta as ta
import plotly.graph_objects as go

from backtesting import Backtest, Strategy
from matplotlib import pyplot as plt
from tqdm import tqdm

### Overarching Constants

In [25]:
ticker = 'BTC-USD'
start = '2023-01-01'
end = '2024-01-01'
interval = '1h'

columns_open = 'Open'
columns_high = 'High'
columns_low = 'Low'
columns_close = 'Close'
columns_volume = 'Volume'
columns_rsi = 'RSI'
columns_ema_slow = 'EMA_Slow'
columns_ema_fast = 'EMA_Fast'
columns_atr = 'ATR'
column_signal_ema = 'EMA_Signal'
columns_simple_scalp = 'Simple_Scalp'

refresh_cache=False
back_candle_length = 7

### Make sure we have some data to work with

In [26]:
if not cache.exist_sql_db(ticker, interval) or refresh_cache:
    # load data from yahoo finance and cache it in sql db
    cache.cache_ticker(ticker, interval, start, end)

# Load data from sql db
df = cache.load_ticker(ticker, interval, start, end, index_column='Date')

#df

### Add TA Columns

In [27]:
df[columns_ema_slow] = ta.ema(df[columns_close], length=50)
df[columns_ema_fast] = ta.ema(df[columns_close], length=30)
df[columns_rsi] = ta.rsi(df[columns_close], length=10)

# Average True Range (or Volatility) - help to define stop loss / take profit distance
df[columns_atr] = ta.atr(df[columns_high], df[columns_low], df[columns_close], length=back_candle_length)

# Bollinger bands
df=df.join(ta.bbands(df[columns_close], length=15, std=1.5))

#df

### Plot

In [ ]:
df.plot(
  y=[
    columns_close, 
    columns_ema_slow, 
    columns_ema_fast, 
    columns_atr,
    'BBL_15_1.5', 
    'BBM_15_1.5', 
    'BBU_15_1.5'
  ])

### EMA signal function

In [28]:
# Needed for progress_apply
tqdm.pandas()

df.reset_index(inplace=True)

# At current candle: Check if all EMA_Fast values are:
# Below EMA_Slow = 2  => Sell
# Above EMA_Slow = 1 => Buy
df[column_signal_ema] = df.progress_apply(
  lambda row: curve.above_or_below_curve(
    df, row.name, back_candle_length,
    curve=columns_ema_fast,
    compare=columns_ema_slow,
    ), 
  axis=1
)

#df

100%|██████████| 8676/8676 [00:02<00:00, 3008.10it/s]


### Plot

In [ ]:
df.plot(
  y=[
    columns_close, 
    columns_ema_slow, 
    columns_ema_fast, 
    columns_atr,
  ])

plt.show()

df.plot(
  y=[
    column_signal_ema,
  ])

plt.show()

### Calculate the Simple Scalping Signal

In [29]:
df[columns_simple_scalp] = df.progress_apply(
  lambda row: simple_scalping.simple_signal(
    df, row.name, 
    back_candle_length,
    ema_fast=columns_ema_fast,
    ema_slow=columns_ema_slow,
    bollinger_low='BBL_15_1.5',
    bollinger_high='BBU_15_1.5',    
    ), axis=1
)

df[df[columns_simple_scalp] != 0].head(40)

100%|██████████| 8676/8676 [00:06<00:00, 1358.53it/s]


Date          Open          High           Low  \
63  2023-01-03 15:00:00  16687.105469  16687.105469  16639.509766   
64  2023-01-03 16:00:00  16667.441406  16685.496094  16630.984375   
65  2023-01-03 17:00:00  16629.419922  16641.076172  16622.371094   
92  2023-01-04 20:00:00  16840.978516  16847.107422  16802.753906   
105 2023-01-05 09:00:00  16814.126953  16816.832031  16798.621094   
109 2023-01-05 13:00:00  16831.501953  16831.501953  16799.576172   
124 2023-01-06 04:00:00  16836.921875  16838.599609  16809.076172   
125 2023-01-06 05:00:00  16824.316406  16824.316406  16807.644531   
126 2023-01-06 06:00:00  16814.363281  16815.222656  16792.867188   
127 2023-01-06 07:00:00  16793.988281  16801.128906  16786.556641   
129 2023-01-06 09:00:00  16808.511719  16808.511719  16772.902344   
130 2023-01-06 10:00:00  16791.537109  16797.580078  16777.953125   
131 2023-01-06 11:00:00  16777.484375  16777.484375  16738.066406   
132 2023-01-06 12:00:00  16748.214844  16748.453125  16727.162109   
155 2023-01-07 11:00:00  16928.953125  16928.953125  16916.083984   
156 2023-01-07 12:00:00  16924.058594  16924.058594  16914.191406   
180 2023-01-08 12:00:00  16938.916016  16938.916016  16932.001953   
255 2023-01-11 15:00:00  17416.652344  17432.740234  17337.994141   
256 2023-01-11 16:00:00  17341.826172  17369.035156  17340.419922   
278 2023-01-12 14:00:00  18277.402344  18317.617188  17995.203125   
338 2023-01-15 02:00:00  20778.130859  20800.722656  20697.730469   
344 2023-01-15 08:00:00  20737.060547  20750.960938  20632.109375   
368 2023-01-16 08:00:00  21121.642578  21121.642578  20782.265625   
423 2023-01-18 15:00:00  21425.060547  21515.003906  21028.021484   
424 2023-01-18 16:00:00  21031.539062  21033.373047  20541.544922   
425 2023-01-18 17:00:00  20684.919922  21074.154297  20684.919922   
428 2023-01-18 20:00:00  20922.708984  20935.126953  20749.441406   
447 2023-01-19 15:00:00  20788.865234  20904.275391  20788.865234   
448 2023-01-19 16:00:00  20876.683594  20911.125000  20850.650391   
450 2023-01-19 18:00:00  20841.896484  20967.933594  20841.896484   
451 2023-01-19 19:00:00  20971.755859  21113.689453  20959.933594   
452 2023-01-19 20:00:00  21104.021484  21163.011719  21076.783203   
503 2023-01-21 23:00:00  23055.214844  23055.214844  22775.570312   
505 2023-01-22 01:00:00  22881.119141  22881.119141  22746.578125   
506 2023-01-22 02:00:00  22807.580078  22823.378906  22696.886719   
523 2023-01-22 19:00:00  22845.552734  22848.082031  22785.095703   
524 2023-01-22 20:00:00  22768.326172  22768.326172  22435.595703   
525 2023-01-22 21:00:00  22457.011719  22610.203125  22387.900391   
565 2023-01-24 13:00:00  22981.587891  23009.253906  22849.175781   
574 2023-01-24 22:00:00  22908.009766  22912.640625  22730.181641   

            Close     Adj Close      Volume      EMA_Slow      EMA_Fast  \
63   16665.871094  16665.871094   548231168  16669.361155  16701.594501   
64   16630.984375  16630.984375   389563392  16667.856183  16697.039009   
65   16630.164062  16630.164062   271706112  16666.378061  16692.724496   
92   16804.451172  16804.451172   293746688  16766.288644  16806.371475   
105  16804.048828  16804.048828           0  16793.855829  16821.933691   
109  16801.863281  16801.863281   276144128  16798.748156  16823.014460   
124  16823.570312  16823.570312   125524992  16818.564278  16835.162157   
125  16814.693359  16814.693359   102779904  16818.412477  16833.841589   
126  16792.867188  16792.867188    55029760  16817.410701  16831.198079   
127  16798.263672  16798.263672           0  16816.659837  16829.073279   
129  16791.695312  16791.695312           0  16815.390317  16825.447234   
130  16777.953125  16777.953125     2803712  16813.922191  16822.383098   
131  16747.888672  16747.888672   441678848  16811.332642  16817.577006   
132  16738.406250  16738.406250   106707968  16808.472783  16812.469215   
155  16924.556641  16924.556641           0  16873.574323  16898

### Set back to datetime index (from range index)

In [30]:
df.set_index('Date', inplace=True)

### Create Dots for Simple Scalping Signals

In [31]:
def render_short_long_signal_point(row: pd.Series, column_name:str) -> str:
  if row[column_name] == simple_scalping.LONG_SIGNAL:
    return row[columns_low]-1e-3
  elif row[column_name] == simple_scalping.SHORT_SIGNAL:
    return row[columns_high]+1e-3
  
  return np.nan

df['ss_point'] = df.apply(lambda row: render_short_long_signal_point(row, columns_simple_scalp), axis=1)

### Plot the Graph

In [32]:
partition = df

fig = go.Figure(data=[go.Candlestick(x=partition.index,
                open=partition[columns_open],
                high=partition[columns_high],
                low=partition[columns_low],
                close=partition[columns_close]),
                
                go.Scatter(x=partition.index, y=partition['BBL_15_1.5'], 
                           line=dict(color='blue', width=1), 
                           name='BBL'),

                go.Scatter(x=partition.index, y=partition['BBU_15_1.5'],
                            line=dict(color='blue', width=1),
                            name='BBU'),

                go.Scatter(x=partition.index, y=partition[columns_ema_slow],
                            line=dict(color='orange', width=1),
                            name='EMA Slow'),

                go.Scatter(x=partition.index, y=partition[columns_ema_fast],
                            line=dict(color='green', width=1),
                            name='EMA Fast'),

                go.Scatter(x=partition.index, y=partition[columns_rsi],
                            line=dict(color='red', width=1),
                            name='RSI'),
                ])

fig.add_trace(go.Scatter(x=partition.index, y=partition['ss_point'],
                            mode='markers', marker=dict(color='darkorange', size=5),
                            name=columns_simple_scalp))

### Backtesting

In [33]:
def signal():
    return df[columns_simple_scalp]

class MyStrategy(Strategy):
    # Stop loss coefficient
    sl_coef = 1.1
    tpsl_ratio = 1.5

    def init(self):
        super().init()

        self.simple_scalp_signal = self.I(signal)

    def next(self):
        super().next()

        # Stop-loss distance
        sl_atr = self.sl_coef * self.data.ATR[-1]
        tpsl_ratio = self.tpsl_ratio

        
        if self.simple_scalp_signal == simple_scalping.LONG_SIGNAL and len(self.trades) == 0:
            sl1 = self.data[columns_close][-1] - sl_atr
            tp1 = self.data[columns_close][-1] + sl_atr * tpsl_ratio
            self.buy(sl=sl1, tp=tp1)

        if self.simple_scalp_signal == simple_scalping.SHORT_SIGNAL and len(self.trades) == 0:
            sl1 = self.data[columns_close][-1] + sl_atr
            tp1 = self.data[columns_close][-1] - sl_atr * tpsl_ratio
            self.sell(sl=sl1, tp=tp1)

bt = Backtest(df, MyStrategy, cash=100000)

bt.run()

Start                     2023-01-01 00:00:00
End                       2023-12-31 23:00:00
Duration                    364 days 23:00:00
Exposure Time [%]                   35.707699
Equity Final [$]                146552.947625
Equity Peak [$]                 147510.038653
Return [%]                          46.552948
Buy & Hold Return [%]              155.481638
Return (Ann.) [%]                   46.706916
Volatility (Ann.) [%]               21.059503
Sharpe Ratio                         2.217855
Sortino Ratio                        4.844996
Calmar Ratio                         6.066537
Max. Drawdown [%]                   -7.699106
Avg. Drawdown [%]                   -0.844229
Max. Drawdown Duration       80 days 21:00:00
Avg. Drawdown Duration        3 days 14:00:00
# Trades                                  491
Win Rate [%]                        45.417515
Best Trade [%]                       3.047278
Worst Trade [%]                     -1.735033
Avg. Trade [%]                    

### Plot the Backtesting Results

In [ ]:
bt.plot()